In [1]:
import streamlit as st
from PIL import Image
from skimage import data
from skimage import transform
from skimage.feature import blob_log
from matplotlib import pyplot as plt
from skyfield.api import Star, Topos, load
from skyfield.data import hipparcos
import numpy as np
import os
import time
import pickle
from plotly.offline import plot, iplot, init_notebook_mode
import plotly.graph_objs as go
from datetime import datetime
import warnings
warnings.filterwarnings('ignore')

with load.open(hipparcos.URL) as f:
    df = hipparcos.load_dataframe(f)

In [2]:
stardict = {}
with open('common_stars.txt') as f:
    lines = f.readlines()
    for line in lines:
        entry = line.strip().split("\t")
        stardict[int(entry[1])] = entry[0]
        stardict[int(entry[3])] = entry[2]

df = df[df['magnitude'] <= 3.0]
print('After filtering, there are {} stars'.format(len(df)))
bright_stars = Star.from_dataframe(df)

planets = load('de421.bsp')
earth = planets['earth']
ts = load.timescale()


After filtering, there are 177 stars


In [3]:
def fish2cylindrical(x,y, f, zoom):
#     f = 10.5/23.6*W
    long = x/f/zoom
    lat = np.arctan(y/f/zoom)
    xx = np.cos(lat) * np.sin(long)
    yy = np.sin(lat)
    phi = np.arctan2(yy,xx)
    theta = np.arcsin(np.sqrt(xx*xx + yy*yy))
    mag = 2*f*np.sin(theta/2)
#     return mag, phi
    return mag*np.cos(phi), mag*np.sin(phi)

def cylindrical2fish(x,y, f, zoom):
#     f = 10.5/23.6*W
    theta = np.arcsin(np.sqrt(x*x + y*y) / (2*f))
    mag = np.sin(theta * 2) # = np.sqrt(xx*xx+yy*yy)
    phi = np.arctan2(y,x)
    xx = mag*np.cos(phi)
    yy = mag*np.sin(phi)
    lat = np.arcsin(yy)
    long = np.arcsin(xx / np.cos(lat))
    y = (f / zoom)*np.tan(lat)
    x = long * f / zoom
    return x,y

def fish2mercator(x,y, f, zoom):
#     f = 10.5/23.6*W
    long = x/f/zoom
    lat = np.arctan(np.sinh(y/f/zoom))
    xx = np.cos(lat) * np.sin(long)
    yy = np.sin(lat)
    phi = np.arctan2(yy,xx)
    theta = np.arcsin(np.sqrt(xx*xx + yy*yy))
    mag = 2*f*np.sin(theta/2)
#     return mag, theta
    return mag*np.cos(phi), mag*np.sin(phi)

def mercator2fish(x,y, f, zoom):
#     f = 10.5/23.6*W
    theta = np.arcsin(np.sqrt(x*x + y*y) / (2*f))
    mag = np.sin(theta * 2) # = np.sqrt(xx*xx+yy*yy)
    phi = np.arctan2(y,x)
    xx = mag*np.cos(phi)
    yy = mag*np.sin(phi)
    lat = np.arcsin(yy)
    long = np.arcsin(xx / np.cos(lat))
    y = (f / zoom)*np.arcsinh(np.tan(lat))
    x = long * f / zoom
    return x,y

def fish2equirectangular(x,y, f, zoom):
#     f = 10.5/23.6*W
    long = x/f/zoom
    lat = y/f/zoom
    xx = np.cos(lat) * np.sin(long)
    yy = np.sin(lat)
    phi = np.arctan2(yy,xx)
    theta = np.arcsin(np.sqrt(xx*xx + yy*yy))
    mag = 2*f*np.sin(theta/2)
#     return mag, theta
    return mag*np.cos(phi), mag*np.sin(phi)

def equirectangular2fish(x,y, f, zoom):
#     f = 10.5/23.6*W
    theta = np.arcsin(np.sqrt(x*x + y*y) / (2*f))
    mag = np.sin(theta * 2) # = np.sqrt(xx*xx+yy*yy)
    phi = np.arctan2(y,x)
    xx = mag*np.cos(phi)
    yy = mag*np.sin(phi)
    lat = np.arcsin(yy)
    long = np.arcsin(xx / np.cos(lat))
    y = lat * f / zoom
    x = long * f / zoom
    return x,y

def fish2poly(x,y, k1, k2, k3, k4):
    phi = np.arctan2(y,x)
    mag = np.sqrt(x**2 + y**2)
    nmag = k1*mag**3 + k2*mag**2 + k3*mag + k4
    return nmag*np.cos(phi), nmag*np.sin(phi)

In [4]:
# fig, ax = plt.subplots(1, 1, figsize=(80, 80), sharex=True, sharey=True)

allblobs = pickle.load( open( "blobs.p", "rb" ) )

# print(len(allblobs))
plots = []
centerx = 1585 / 2172 - 0.5
centery = (1411 - 655) / 2172 - 0.5*1411/2172

for pic,blobs_log in enumerate(allblobs):
    starblobs = blobs_log[np.where(blobs_log[:,2] <= 4)]
    if pic % 10 == 0:
        blobx = starblobs[:, 1] / 2172 - 0.5
        bloby = (1411 - starblobs[:, 0])/2172  - 0.5*1411/2172
        bstring = [str(x) for x in range(len(blobx))]
        plots.append(
            go.Scatter(x=blobx, y=bloby, mode='markers', text=bstring, name=f"{pic}")
        )
layout = go.Layout(
    height = 800,
    width = 800
)

fig = go.Figure(data=plots, layout=layout)
iplot(fig)


In [5]:
# blobx = starblobs[:, 1] / 2172 - 0.5
# bloby = (1411 - starblobs[:, 0])/ 2172 - 0.5
nblobs = []
for bb in allblobs:
    xy = bb[:,1::-1].copy()
#     print(bb[:10,3])
#     xy = xy[np.where(bb[:,3] < 2)]
    xy[:,0] = xy[:,0] / 2172 - 0.5
    xy[:,1] = (1411 - xy[:,1]) / 2172 - 0.5*1411/2172
    nblobs.append(xy)

# f = 0.94 # cylindrical
f = 0.77802066 # mercator
# f = 0.83940173 # fish2equirectangular
centerx = 1585 / 2172 - 0.5
centery = (1411 - 655) / 2172 - 0.5*1411/2172    

# centerx,centery = fish2mercator(centerx,centery,f,1)

print("center is",centerx, centery)

centerx = 0.23788478
centery = 0.02541838
# centerx,centery = fish2mercator(centerx,centery,f,1)

tcart = nblobs[1:]
firstcart = nblobs[0]

print(firstcart.shape)
print(len(allblobs))

plots = []
starlines = []

squarer = lambda t: t + 2*np.pi if t < 0 else t
vfunc = np.vectorize(squarer)

while len(firstcart) > 0:
# if True:
    for cnt,val in enumerate(firstcart):
        stringx = []
        stringy = []

        now = val
        avs = []
        for test in tcart:
            dist = np.sqrt((now[0]-test[:,0])**2 + (now[1]-test[:,1])**2)
            mm = np.argmin(dist)
            avs.append(dist[mm])
            now = test[mm,:]
        avs = np.array(avs)
        av = np.average(avs)
        std = np.std(avs)

        now = val
        avs = []
        for test in tcart:
            dist = np.sqrt((now[0]-test[:,0])**2 + (now[1]-test[:,1])**2)
            mm = np.argmin(dist)
            if dist[mm] > (av - 2*std) and dist[mm] < (av + 2*std):
                avs.append(dist[mm])
            now = test[mm,:]
        avs = np.array(avs)
        av = np.average(avs)
        std = np.std(avs)

        now = val.copy()
        stringx.append(now[0])
        stringy.append(now[1])
        
        for test in tcart:
            # this needs to be improved to track star velocities
            # right not it is just averages
            dist = np.sqrt((now[0]-test[:,0])**2 + (now[1]-test[:,1])**2)
            mm = np.argmin(dist)
            if not (dist[mm] > (av - 2*std) and dist[mm] < (av + 2*std)):
    #         if dist[mm] > 0.008:
                break
            now = test[mm,:].copy()
            test[mm,:] *= 0
            stringx.append(now[0])
            stringy.append(now[1])
#         vcart = []
#         for test in tcart:
#             test = test[np.where(np.isfinite(test[:,0]))]
#             vcart.append(test)
#         tcart = vcart
        if len(stringx) > 20:
            totaldist = np.sqrt((stringx[0] - stringx[-1])**2 + (stringy[0] - stringy[-1])**2)
            if totaldist > 0:
                starlines.append([*zip(stringx,stringy)])
                xx,yy = fish2mercator(np.array(stringx),np.array(stringy),f,1)
#                 xx,yy = [np.array(stringx),np.array(stringy)]
                sxx = xx - centerx
                syy = yy - centery
                ang = np.arctan2(syy,sxx)
                ang = vfunc(ang)
                mag = np.sqrt(sxx*sxx + syy*syy)
#                 mag[1:] = (mag[1:] - mag[:-1])
                mag -= np.average(mag)
                plots.append(go.Scatter(x=ang, y=mag))
#                 plots.append(go.Scatter(x=stringx, y=stringy))
    if len(nblobs) > 40:
#         print(len(nblobs))
        nblobs.pop(0)
        tcart = nblobs[1:]
        firstcart = nblobs[0]
    else:
        firstcart = []

print("Total lines", len(starlines))

fig = go.Figure(data=plots, layout=layout)
iplot(fig)


center is 0.2297421731123389 0.023250460405156548
(147, 2)
180
Total lines 265


In [13]:
plots = []
# f = 0.8337693
# centerx = 0.23629585
# centery = 0.02670125

f = 0.46633968
centerx = 0.13437445
centery = 0.01284811

for line in starlines:
    stringx, stringy = zip(*line)
    xx,yy = fish2cylindrical(np.array(stringx),np.array(stringy),f,1.8)
#     xx,yy = [np.array(stringx),np.array(stringy)]
    sxx = xx - centerx
    syy = yy - centery
    ang = np.arctan2(syy,sxx)
    ang = vfunc(ang)
    mag = np.sqrt(sxx*sxx + syy*syy)
#                 mag[1:] = (mag[1:] - mag[:-1])
    mag -= np.average(mag)
    plots.append(go.Scatter(x=ang, y=mag))
fig = go.Figure(data=plots, layout=layout)
iplot(fig)


In [7]:
pickle.dump( starlines, open( "starlines.p", "wb" ) )